Natural Convection
===

Coupling of Navier-Stokes and heat transport

* Change in temperature leads to gravity forces
* Temperature is convected by fluid velocity

Rayleigh-Benard benchmark example

In [ ]:
from ngsolve import *
from netgen.occ import *
from ngsolve.webgui import Draw
import ipywidgets as widgets

from ngs_templates.NavierStokes import *
from ngs_templates.ConvectionDiffusion import * 

ngsglobals.msg_level = 0

In [ ]:
shape = Rectangle(0.06,0.01).Face()
shape.edges.Min(Y).name = 'b'
shape.edges.Max(Y).name = 't'
mesh = Mesh(OCCGeometry(shape, dim=2).GenerateMesh(maxh=0.002)).Curve(3)

In [ ]:
timestep = 0.1
navstokes = NavierStokes (mesh, nu=1.04177e-6, order=3, timestep = timestep,
                              inflow="", outflow="", wall=".*", uin=(0,0) )

Tinitial = 293.5-50*y+y*(0.01-y)*1e3*sin(20/0.06*x*pi)

convdiff = ConvectionDiffusionEquation (mesh, order=3, lam=1.38e-7, \
                wind = navstokes.velocity, dirichlet="b|t", udir=Tinitial, timestep=timestep)
convdiff.SetInitial(Tinitial)

T0 = 293
beta = 2.07e-4
navstokes.AddForce ( (1-beta*(convdiff.concentration-T0))*(0, -9.81))

navstokes.SolveInitial()

In [ ]:
tw = widgets.Text(value='t = 0')
display(tw)

scenev = Draw (navstokes.velocity, mesh, "velocity", vectors = { "grid_size" : 40 })
scenet = Draw (convdiff.concentration, mesh, "temp")

t, tend = 0, 1000
cnt = 0
with TaskManager():
    while t < tend:
        navstokes.DoTimeStep()
        convdiff.DoTimeStep()
        t = t+timestep
        cnt = cnt+1
        if cnt % 10 == 0:           
            tw.value = "t = "+str(t)
            scenev.Redraw()
            scenet.Redraw()